# Отчет об использовании прокатных велосипедов в районах НЙ

In [23]:
import pandas as pd
import datetime
import calendar
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import json

import matplotlib.pyplot as plt

import os
import conda

import os
import conda

conda_file_dir = conda.__file__
conda_dir = conda_file_dir.split('lib')[0]
proj_lib = os.path.join(os.path.join(conda_dir, 'Lib'), 'site-packages\mpl_toolkits\\basemap\data')
os.environ["PROJ_LIB"] = proj_lib
import mpl_toolkits.basemap as bm


# настройка отображения графиков plotly
import plotly.io as pio
pio.renderers.default='notebook'

In [2]:
df_jun = pd.read_csv('datas/201906-citibike-tripdata.csv')

## Постановка задачи

Задание звучит так:<br><b>"Раскрыть временное распределение поездок и попытаться рассказать небольшую историю о различии или схожести районов."</b>
<p>Так как задание звучит не вполне четко, попытаемся его как-то интерпретировать и разбить на более конкретные подзадачи.</p>

### Интерпретация задачи и разбитие на подзадачи

<p>Фраза <b>"Раскрыть временное распределение"</b> подразумевает, что нужно поездки разделять по времени в зависимости от каких-то факторов.</p>
<p>Фраза <b>"попытаться рассказать небольшую историю о различии или схожести районов"</b> более сложная за счет большей свободы размышления.<br>Я эту задачу разбил на подзадачи и решил ответить на ряд вопросов:</p>
<ol>
    <li>Самые часто\редко посещаемые районы для старта\финиша на прокатном велосидепе</li>
    <li>Где начинаются и заканчиваются самые продолжительные прокаты</li>
    <li>Просмотреть данные по районам за несколько месяцев (разные сезоны)</li>
    <li>Где катаются дольше по времени</li>
    <li>В зависимости от возраста клиентов, надо посмотреть на карте наличие школ, университетов и т.д. Откуда могут приходить клиенты</li>
    <li>На основе bikeid можно предсказать самые популярные модели велосипедов</li>
    <li>Так же нам дана карта. После анализа районов, нужно посмотреть по карте на наличие парков или спец. площадок/дорожек для велосипедистов</li>
</ol>

## Решение

Сначала озвучу несколько идей, которые возможно пригодятся в будущем:
<ul>
    <li>Может дли велосипед использоваться для объезда пробок (когда время использования велосипеда очень маленькое)?</li>
    <li>Используется ли велосипед просто для поездки от дома до метро?</li>
    <li>По кол-ву велосипедов на станции возможно ли определить деловой район или для досуга\отдыха?</li>
    <li>Есть ли среди клиентов курьеры?</li>
</ul>
<hr>

### Задача временного распределения (реализация с помощью plotly)

Сначала попытаемся раскрыть временное распределение поездок.<br>
<ol>Рассмотрим 2 категории деления времени:
    <li><i>По дням в течение недели</i> (будни или выходные)</li>
    <li><i>По часам в течение дня</i> (рабочее время, ночное, вечернее)</li>
</ol>
Также для точности данных рассмотрим данные за разные сезоны: <i>лето (июнь)</i> и <i>зиму (декабрь)</i>.

#### Летнее время

In [3]:
df_jun.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2125370 entries, 0 to 2125369
Data columns (total 15 columns):
 #   Column                   Dtype  
---  ------                   -----  
 0   tripduration             int64  
 1   starttime                object 
 2   stoptime                 object 
 3   start station id         int64  
 4   start station name       object 
 5   start station latitude   float64
 6   start station longitude  float64
 7   end station id           int64  
 8   end station name         object 
 9   end station latitude     float64
 10  end station longitude    float64
 11  bikeid                   int64  
 12  usertype                 object 
 13  birth year               int64  
 14  gender                   int64  
dtypes: float64(4), int64(6), object(5)
memory usage: 243.2+ MB


Преобразуем некоторые колонки в формат даты и добавим новые столбцы со значениями дней недели начала и конца поездки

In [4]:
# преобразуем в формат даты
df_jun.loc[:, 'starttime'] = pd.to_datetime(df_jun['starttime'])
df_jun.loc[:, 'stoptime'] = pd.to_datetime(df_jun['stoptime'])

# добавим столбец со значением дня недели старта проката
df_jun.loc[:, 'startday'] = [calendar.day_abbr[calendar.weekday(
    day.year, day.month, day.day)] for day in df_jun['starttime']]
# добавим столбец со значением дня недели конца проката
df_jun.loc[:, 'stopday'] = [calendar.day_abbr[calendar.weekday(
    day.year, day.month, day.day)] for day in df_jun['stoptime']]

Построим графики, который покажут в какой день чаще катаются на велосипедах.<br>
<i>Для чистоты данных возьмем поездки, не превышающие продолжительности суток и рассмотрим графики для начала и конца поездки: вдруг они разительно отличаются. Также построим график для всех поездок</i>

In [5]:
df_short_ride = df_jun[df_jun['tripduration'] < 60*60*24] # датафрейм с короткими поездками (до 24 часов)

In [6]:
df_short_ride.groupby('startday')['startday'].count()

startday
Fri    307822
Mon    267197
Sat    367552
Sun    335771
Thu    271984
Tue    263577
Wed    310733
Name: startday, dtype: int64

In [7]:
# список дней для облегчения сортировки при выводе
days = ['Mon', 'Tue', 'Wed', 'Thu', 'Fri', 'Sat', 'Sun']

fig = make_subplots(rows=1, cols=2, subplot_titles=('Короткие поездки', 'Все поездки'), shared_yaxes=True)

trace_start_short = go.Scatter(x=days,
                               y=[df_short_ride.groupby('startday')['startday'].count()[day] for day in days],
                               name='Начало проката',
                               line={'color': 'red'},
                               )
trace_finish_short = go.Scatter(x=days,
                                y=[df_short_ride.groupby('stopday')['stopday'].count()[day] for day in days],
                                name='Конец проката',
                                line={'color': 'blue'},
                                )
trace_start_all = go.Scatter(x=days,
                             y=[df_jun.groupby('startday')['startday'].count()[day] for day in days],
                             name='Начало проката',
                             line={'color': 'red'},
                             showlegend=False,
                             )
trace_finish_all = go.Scatter(x=days,
                              y=[df_jun.groupby('stopday')['stopday'].count()[day] for day in days],
                              showlegend=False,
                              name='Конец проката',
                              line={'color': 'blue'},
                              )

layout = {'title': {'text': 'График поездок в зависимости от дня недели летом', 'x': 0.5},
          'xaxis': {'title': 'Дни недели'},
          'xaxis2': {'title': 'Дни недели'},
          'yaxis_title': 'Кол-во поездок, шт.'}

pics = [[trace_start_short, trace_finish_short], [trace_start_all, trace_finish_all]]

fig.add_trace(pics[0][0], 1, 1)
fig.add_trace(pics[0][1], 1, 1)
fig.add_trace(pics[1][0], 1, 2)
fig.add_trace(pics[1][1], 1, 2)

fig.update_layout(layout)

fig.show()

<b>Чаше всего катаются конечно на выходных (Суббота и воскресение).</b><br>
Графики не сильно различаются в зависимости от начала или конца поездки, а также от продолжительности поездки.

Теперь рассмотрим распределение по часам в течение суток. Для удобства также можем добавить столбцы в наш датафрейм

In [8]:
df_jun.loc[:,'starthour'] = [day.hour for day in df_jun['starttime']]
df_jun.loc[:,'stophour'] = [day.hour for day in df_jun['stoptime']]

Построим 2 графика: 1 будет показывать во сколько чаще всего начинают прокат, а 2 покажет когда его чаще всего завершают.<br>
<i>Для чистоты данных, возьмем поездки не короче 5-ти минут</i>

In [9]:
# Рабочее время
work_start = df_jun[(df_jun['starthour'].isin(range(9, 18+1))) &
                    (df_jun['tripduration'] < 60*5)].groupby('starthour')['starthour'].count()
work_stop = df_jun[(df_jun['stophour'].isin(range(9, 18+1))) &
                   (df_jun['tripduration'] < 60*5)].groupby('stophour')['stophour'].count()
# Время после работы
rest_start = df_jun[(df_jun['starthour'].isin(range(18, 23+1))) &
                    (df_jun['tripduration'] < 60*5)].groupby('starthour')['starthour'].count()
rest_stop = df_jun[(df_jun['stophour'].isin(range(18, 23+1))) &
                   (df_jun['tripduration'] < 60*5)].groupby('stophour')['stophour'].count()
# Ночное время
night_start = df_jun[(df_jun['starthour'].isin(range(0, 5+1))) &
                     (df_jun['tripduration'] < 60*5)].groupby('starthour')['starthour'].count()
night_stop = df_jun[(df_jun['stophour'].isin(range(0, 5+1))) &
                    (df_jun['tripduration'] < 60*5)].groupby('stophour')['stophour'].count()
# Утреннее время
morning_start = df_jun[(df_jun['starthour'].isin(range(
    5, 9+1))) & (df_jun['tripduration'] < 60*5)].groupby('starthour')['starthour'].count()
morning_stop = df_jun[(df_jun['stophour'].isin(range(
    5, 9+1))) & (df_jun['tripduration'] < 60*5)].groupby('stophour')['stophour'].count()

# Рисуем графики
trace_start_work = go.Scatter(x=work_start.index,
                              y=work_start.values,
                              name='Старт в рабочее время',
                              )
trace_stop_work = go.Scatter(x=work_stop.index,
                             y=work_stop.values,
                             name='Финиш в рабочее время',
                             )

trace_start_rest = go.Scatter(x=rest_start.index,
                              y=rest_start.values,
                              name='Старт в послерабочее время',
                              )
trace_stop_rest = go.Scatter(x=rest_stop.index,
                             y=rest_stop.values,
                             name='Финиш в послерабочее время',
                             )

trace_start_night = go.Scatter(x=night_start.index,
                               y=night_start.values,
                               name='Старт в ночное время',
                               )
trace_stop_night = go.Scatter(x=night_stop.index,
                              y=night_stop.values,
                              name='Финиш в ночное время',
                              )

trace_start_morning = go.Scatter(x=morning_start.index,
                                 y=morning_start.values,
                                 name='Старт в утренне время',
                                 )
trace_stop_morning = go.Scatter(x=morning_stop.index,
                                y=morning_stop.values,
                                name='Финиш в утренне время',
                                )

layout = {'title': {'text': 'График распределения поездок в течение дня летом', 'x': 0.5},
          'xaxis_title': 'Часы',
          'yaxis_title': 'Кол-во поездок, шт.',
         }


data = [trace_start_work, trace_stop_work,
        trace_start_rest, trace_stop_rest,
        trace_start_night, trace_stop_night,
        trace_start_morning, trace_stop_morning]
go.Figure(data=data, layout=layout).show()

Графики стартов и завершений проката практически идентичны.<br>
Заметны пики в значениях 8 утра, 13 дня и 17-18 часов вечера.<br>
<b>Можно предположить, что в 8 часов люди едут на работу, в 13 дня едут на обед, а в 17-18 часов вечера едут с работы.</b>
<hr>

#### Зимнее время

Проделаем тоже самое с другим периодом времени и выясним, есть ли различия

In [10]:
df_dec = pd.read_csv('datas/201912-citibike-tripdata.csv')

In [11]:
# преобразуем в формат даты
df_dec.loc[:, 'starttime'] = pd.to_datetime(df_dec['starttime'])
df_dec.loc[:, 'stoptime'] = pd.to_datetime(df_dec['stoptime'])

# добавим столбец со значением дня недели старта проката
df_dec.loc[:, 'startday'] = [calendar.day_abbr[calendar.weekday(
    day.year, day.month, day.day)] for day in df_dec['starttime']]
# добавим столбец со значением дня недели конца проката
df_dec.loc[:, 'stopday'] = [calendar.day_abbr[calendar.weekday(
    day.year, day.month, day.day)] for day in df_dec['stoptime']]

# добавим столбцы со значениями часа начала и конца проката
df_dec.loc[:,'starthour'] = [day.hour for day in df_dec['starttime']]
df_dec.loc[:,'stophour'] = [day.hour for day in df_dec['stoptime']]

In [12]:
df_short_ride = df_dec[df_dec['tripduration'] < 60*60*24] # датафрейм с короткими поездками (до 24 часов)

In [13]:
# 1 график
trace_start_short = go.Scatter(x=days,
                               y=[df_short_ride.groupby('startday')['startday'].count()[day] for day in days],
                               name='Начало проката',
                               line={'color': 'red'},
                               )
trace_finish_short = go.Scatter(x=days,
                                y=[df_short_ride.groupby('stopday')['stopday'].count()[day] for day in days],
                                name='Конец проката',
                                line={'color': 'blue'},
                                )

In [14]:
# 2 график
trace_start_all = go.Scatter(x=days,
                             y=[df_dec.groupby('startday')['startday'].count()[day] for day in days],
                             name='Начало проката',
                             line={'color': 'red'},
                             showlegend=False,
                             )
trace_finish_all = go.Scatter(x=days,
                              y=[df_dec.groupby('stopday')['stopday'].count()[day] for day in days],
                              name='Конец проката',
                              line={'color': 'blue'},
                              showlegend=False,
                              )

In [15]:
# 3 график
# Рабочее время
work_start = df_dec[(df_dec['starthour'].isin(range(9, 18+1))) &
                    (df_dec['tripduration'] < 60*5)].groupby('starthour')['starthour'].count()
work_stop = df_dec[(df_dec['stophour'].isin(range(9, 18+1))) &
                   (df_dec['tripduration'] < 60*5)].groupby('stophour')['stophour'].count()
# Время после работы
rest_start = df_dec[(df_dec['starthour'].isin(range(18, 23+1))) &
                    (df_dec['tripduration'] < 60*5)].groupby('starthour')['starthour'].count()
rest_stop = df_dec[(df_dec['stophour'].isin(range(18, 23+1))) &
                   (df_dec['tripduration'] < 60*5)].groupby('stophour')['stophour'].count()
# Ночное время
night_start = df_dec[(df_dec['starthour'].isin(range(0, 5+1))) &
                     (df_dec['tripduration'] < 60*5)].groupby('starthour')['starthour'].count()
night_stop = df_dec[(df_dec['stophour'].isin(range(0, 5+1))) &
                    (df_dec['tripduration'] < 60*5)].groupby('stophour')['stophour'].count()
# Утреннее время
morning_start = df_dec[(df_dec['starthour'].isin(range(
    5, 9+1))) & (df_dec['tripduration'] < 60*5)].groupby('starthour')['starthour'].count()
morning_stop = df_dec[(df_dec['stophour'].isin(range(
    5, 9+1))) & (df_dec['tripduration'] < 60*5)].groupby('stophour')['stophour'].count()

trace_start_work = go.Scatter(x=work_start.index,
                              y=work_start.values,
                              name='Старт в рабочее время',
                              )
trace_stop_work = go.Scatter(x=work_stop.index,
                             y=work_stop.values,
                             name='Финиш в рабочее время',
                             )

trace_start_rest = go.Scatter(x=rest_start.index,
                              y=rest_start.values,
                              name='Старт в послерабочее время',
                              )
trace_stop_rest = go.Scatter(x=rest_stop.index,
                             y=rest_stop.values,
                             name='Финиш в послерабочее время',
                             )

trace_start_night = go.Scatter(x=night_start.index,
                               y=night_start.values,
                               name='Старт в ночное время',
                               )
trace_stop_night = go.Scatter(x=night_stop.index,
                              y=night_stop.values,
                              name='Финиш в ночное время',
                              )

trace_start_morning = go.Scatter(x=morning_start.index,
                                 y=morning_start.values,
                                 name='Старт в утренне время',
                                 )
trace_stop_morning = go.Scatter(x=morning_stop.index,
                                y=morning_stop.values,
                                name='Финиш в утренне время',
                                )

In [133]:
pics = [[[trace_start_short, trace_finish_short], [trace_start_all, trace_finish_all]],
        [trace_start_work, trace_stop_work, trace_start_rest, trace_stop_rest,
         trace_start_night, trace_stop_night, trace_start_morning, trace_stop_morning]]

fig_w = make_subplots(rows=2, cols=2,
                      specs = [[{},{}],[{'colspan':2}, None]],
                      shared_yaxes=True,
                      subplot_titles=('Короткие поездки', 'Все поездки',
                                      'График распределения поездок в течение дня'),
                     )

layout = {'title': {'text': 'График поездок в зависимости от дня недели зимой',
                    'x': 0.5},
          'xaxis1': {'title': 'Дни недели'},
          'xaxis2': {'title': 'Дни недели'},
          'xaxis3': {'title': 'Время в течение дня',
                     'tickvals': [hour for hour in range(0,23+1)],
                    },
          'yaxis1': {'title':'Кол-во поездок, шт.'},
          'yaxis3': {'title':'Кол-во поездок, шт.'},
          'height' : 700,
         }

fig_w.add_trace(pics[0][0][0], 1, 1)
fig_w.add_trace(pics[0][0][1], 1, 1)
fig_w.add_trace(pics[0][1][0], 1, 2)
fig_w.add_trace(pics[0][1][1], 1, 2)

for i,_ in enumerate(pics[1]):
    fig_w.add_trace(pics[1][i], 2, 1)

fig_w.update_layout(layout)
fig_w.show()

Зимой наблюдаем немного другую картину: <b>Зимой чаще катаются в будни.</b><br>
Что касается распределения в течение дня, то картинка практически не изменилась.

То есть получается, что летом люди берут велосипеды напрокат чаще, чтобы отдыхать, зимой же, скорее всего, на них добираются на работу.

<hr>
<b>Таким образом, мы выяснили, что среди недели чаще катаются по выходным летом и в будни зимой, а в течении дня сущ. несколько пиков, когда велосипеды особенно востребованы</b>

### Задача составления истории о районах

Для того, чтобы добиться объективности данных снова будем рассматривать раздель летние и зимние данные.

In [17]:
# Для ускоренной обработки датафреймов удалим те стобцы,
# что мы добавляли во время работы с временным распределением.
try:
    df_jun.drop(['startday', 'stopday', 'starthour', 'stophour'], axis=1, inplace=True)
    df_dec.drop(['startday', 'stopday', 'starthour', 'stophour'], axis=1, inplace=True)
except:
    pass

#### Самые часто\редко посещаемые районы для старта\финиша на прокатном велосидепе

In [18]:
df_jun.columns.to_list()

['tripduration',
 'starttime',
 'stoptime',
 'start station id',
 'start station name',
 'start station latitude',
 'start station longitude',
 'end station id',
 'end station name',
 'end station latitude',
 'end station longitude',
 'bikeid',
 'usertype',
 'birth year',
 'gender']

In [19]:
with open('datas/district_geography.json') as json_data:
    geomap = json.load(json_data)

In [124]:
geomap # json с географией мест

{'type': 'FeatureCollection',
 'crs': {'type': 'name', 'properties': {'name': 'EPSG:4326'}},
 'features': [{'type': 'Feature',
   'id': 1,
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-73.9729957711089, 40.6088223787091],
      [-73.9725912551753, 40.6066797705023],
      [-73.9723987864982, 40.6056601273862],
      [-73.9721788594566, 40.6042029477302],
      [-73.9723529524159, 40.6033563548238],
      [-73.9724540481467, 40.6026252901246],
      [-73.9725667684261, 40.6018026089175],
      [-73.9729125997271, 40.5993240398377],
      [-73.9729685630975, 40.598918195596],
      [-73.9730225114494, 40.5985270212521],
      [-73.9731242778069, 40.5977987564034],
      [-73.9732412669134, 40.5969870534211],
      [-73.9740853363847, 40.596891179076],
      [-73.9749283873699, 40.5968017730674],
      [-73.9750408357827, 40.5967882617849],
      [-73.9755896246112, 40.5967274412784],
      [-73.9765107765378, 40.5966243441713],
      [-73.9775081743104, 40.5965146880145],
   

In [39]:
coords = geomap['features'][0]['geometry']['coordinates']
coords

[[[-73.9729957711089, 40.6088223787091],
  [-73.9725912551753, 40.6066797705023],
  [-73.9723987864982, 40.6056601273862],
  [-73.9721788594566, 40.6042029477302],
  [-73.9723529524159, 40.6033563548238],
  [-73.9724540481467, 40.6026252901246],
  [-73.9725667684261, 40.6018026089175],
  [-73.9729125997271, 40.5993240398377],
  [-73.9729685630975, 40.598918195596],
  [-73.9730225114494, 40.5985270212521],
  [-73.9731242778069, 40.5977987564034],
  [-73.9732412669134, 40.5969870534211],
  [-73.9740853363847, 40.596891179076],
  [-73.9749283873699, 40.5968017730674],
  [-73.9750408357827, 40.5967882617849],
  [-73.9755896246112, 40.5967274412784],
  [-73.9765107765378, 40.5966243441713],
  [-73.9775081743104, 40.5965146880145],
  [-73.9785031239708, 40.5964030875192],
  [-73.9789071472317, 40.5963609647804],
  [-73.9794273012852, 40.5963057570594],
  [-73.9803592885365, 40.5961997754828],
  [-73.9812852802325, 40.5960961357355],
  [-73.98221259264, 40.5959952452309],
  [-73.9831417809253

In [25]:
def plot_geo(lat,lon, labels=None):
    try:
        lllat, lllon = lat.min()-1,lon.max()+1
        urlat,urlon = lat.max()+1, lot.min()-1
        
        plt.figure(figsize=(10,10))
        
        m = bm.Basemap(
            llcrnrlon=lllon,
            llcrnrlat=lllat,
            urcrnrlon=urlon,
            urcrnrlat=urlat,
            projection='merc',
            resolution='h'
        )
        
        m.drawcoastlines(linewidth=0.5)
        m.drawmapboundary(fill_color='#47A4C9', zorder=1)
        m.fillcontinents(color='#EBC4D8', lake_color='#47A4C9', zorder=2)
        
        parallels = np.linspace(lllat, urlat, 10)
        m.drawparallels(parallels,labels=[1,0,0,0], fontsize = 10)
#         draw meridians
        meridians = np.linspace(urlon,lllon, 10)
        m.drawmeridians(meridians,labels=[0,0,0,1], fontsize = 10)
        
        m.scatter(lon,lat,latlon=True, cmap=plt.cm.jet,
                 zorder=3, lw=0, c=labels)
    except:
        print('Ошибка')
        plt.scatter(x=lon,y=lat,c=labels, cmap=plt.cm.jet)
        plt.axis('equal')

In [122]:
coords_1 = geomap['features'][0]['geometry']['coordinates'][0]
geo_df = pd.DataFrame({'lat' : [coords_1[x][0] for x in range(0, len(coords_1)-1)],
                      'lon' : [coords_1[x][1] for x in range(0, len(coords_1)-1)]})

In [128]:
fig = go.Figure(go.Scattergeo())
fig.update_geos(
    visible=False,
    resolution=110,
    scope='usa',
    showcountries=True,
    countrycolor='gold',
    showsubunits=True,
    subunitcolor='blue'
)
fig.update_layout(height=400, margin={"r":0,"t":0,"l":0,"b":0})
fig.show()